In [3]:
import pyspark
import numpy as np
import pandas as pd
from pyspark.sql.types import *
from pyspark.sql.functions import udf,col,sum, explode, desc, approx_count_distinct

# Plotly visualizations
from plotly import tools
# import plotly.plotly as py
import plotly.figure_factory as ff
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)

#Settings
pd.options.display.max_columns = None
pd.options.display.float_format = '{:.2f}'.format
pd.set_option('display.max_colwidth', -1)
pd.set_option('display.max_rows', 500)
from IPython.core.interactiveshell import InteractiveShell  
InteractiveShell.ast_node_interactivity = "all"
seed = 123
spark = pyspark.sql.SparkSession.builder.getOrCreate()

887,379 obs

In [2]:
fullpath = '../data/raw/loan.csv'

In [3]:
data = spark.read.csv(fullpath,
                     sep=',',
                     inferSchema=True,
                     header=True)

In [12]:
data.agg(approx_count_distinct(data.emp_title).alias('distinct_emp_title')).collect()

[Row(distinct_emp_title=295761)]

In [14]:
data.select(["emp_title",'id']).groupby('emp_title').count().orderBy('count', ascending=False).show(30)

+--------------------+-----+
|           emp_title|count|
+--------------------+-----+
|                null|51457|
|             Teacher|13469|
|             Manager|11240|
|    Registered Nurse| 5525|
|               Owner| 5376|
|                  RN| 5355|
|          Supervisor| 4983|
|               Sales| 4212|
|     Project Manager| 3988|
|              Driver| 3569|
|      Office Manager| 3510|
|     General Manager| 3178|
|            Director| 3156|
|             manager| 3138|
|             teacher| 2925|
|               owner| 2849|
|            Engineer| 2671|
|           President| 2598|
|              driver| 2429|
|      Vice President| 2351|
|            Attorney| 2136|
|  Operations Manager| 2071|
|          Accountant| 2035|
|Administrative As...| 2019|
|       Sales Manager| 1846|
|     Account Manager| 1725|
|               sales| 1724|
|      Police Officer| 1720|
|          supervisor| 1675|
| Executive Assistant| 1603|
+--------------------+-----+
only showing t

In [13]:
data.select(["mths_since_rcnt_il",'id']).groupby('mths_since_rcnt_il').count().orderBy('count', ascending=False).show(30)

+------------------+------+
|mths_since_rcnt_il| count|
+------------------+------+
|              null|866540|
|               4.0|  1232|
|               3.0|  1187|
|               7.0|  1081|
|               5.0|  1049|
|               6.0|   987|
|               2.0|   937|
|               8.0|   897|
|              13.0|   807|
|               9.0|   753|
|              11.0|   720|
|              14.0|   709|
|              12.0|   624|
|              10.0|   566|
|              16.0|   557|
|               1.0|   554|
|              17.0|   545|
|              15.0|   535|
|              18.0|   406|
|              19.0|   403|
|              20.0|   370|
|              21.0|   305|
|              22.0|   252|
|              28.0|   232|
|              24.0|   229|
|              25.0|   210|
|              23.0|   207|
|              26.0|   203|
|              27.0|   197|
|              29.0|   176|
+------------------+------+
only showing top 30 rows



In [15]:
data.select(["max_bal_bc",'id']).groupby('max_bal_bc').count().orderBy('count', ascending=False).show(30)

+----------+------+
|max_bal_bc| count|
+----------+------+
|      null|865993|
|       0.0|   411|
|    2968.0|    11|
|    2098.0|    10|
|    4900.0|    10|
|    3906.0|     9|
|    2195.0|     9|
|    2430.0|     9|
|    2000.0|     9|
|    2924.0|     9|
|    1401.0|     9|
|    4000.0|     8|
|    2997.0|     8|
|    6300.0|     8|
|    1467.0|     8|
|    1900.0|     8|
|    2981.0|     8|
|    3958.0|     8|
|    1675.0|     8|
|    2437.0|     8|
|    1055.0|     8|
|    3973.0|     8|
|    2801.0|     8|
|    3562.0|     8|
|    2265.0|     8|
|    2730.0|     8|
|    1969.0|     8|
|    1134.0|     7|
|    3455.0|     7|
|    3563.0|     7|
+----------+------+
only showing top 30 rows



In [16]:
data.select(["total_acc",'id']).groupby('total_acc').count().orderBy('count', ascending=False).show(30)

+---------+-----+
|total_acc|count|
+---------+-----+
|     22.0|32249|
|     20.0|32111|
|     21.0|31999|
|     19.0|31562|
|     23.0|31307|
|     18.0|31106|
|     24.0|31036|
|     17.0|30759|
|     25.0|29711|
|     16.0|29121|
|     26.0|29008|
|     15.0|27927|
|     27.0|27620|
|     14.0|26285|
|     28.0|26143|
|     29.0|25013|
|     13.0|24705|
|     30.0|23790|
|     12.0|22113|
|     31.0|21992|
|     32.0|20953|
|     11.0|19933|
|     33.0|19093|
|     34.0|17883|
|     10.0|17405|
|     35.0|16450|
|     36.0|15204|
|      9.0|14682|
|     37.0|14093|
|     38.0|12586|
+---------+-----+
only showing top 30 rows



In [17]:
data.select(["verification_status",'id']).groupby('verification_status').count().orderBy('count', ascending=False).show(30)

+-------------------+------+
|verification_status| count|
+-------------------+------+
|    Source Verified|329557|
|           Verified|291071|
|       Not Verified|266750|
|            38000.0|     1|
+-------------------+------+



In [18]:
data.select(["verification_status_joint",'id']).groupby('verification_status_joint').count().orderBy('count', ascending=False).show(30)

+-------------------------+------+
|verification_status_joint| count|
+-------------------------+------+
|                     null|886744|
|             Not Verified|   283|
|                 Verified|   167|
|          Source Verified|    61|
|               INDIVIDUAL|    39|
|                      1.0|    22|
|                      0.0|    20|
|                 Jan-2011|     4|
|                 Dec-2012|     2|
|                 Jan-2016|     2|
|                 Mar-2012|     2|
|                     2.61|     1|
|                 Feb-2013|     1|
|                   7390.1|     1|
|                      6.0|     1|
|                        f|     1|
|                  5342.91|     1|
|                 Jul-2013|     1|
|                  18252.0|     1|
|                    25.46|     1|
|                  1822.88|     1|
|                  18610.0|     1|
|                 Dec-2010|     1|
|                  8656.75|     1|
|                 12299.61|     1|
|                 Ju

In [19]:
data.select(["application_type",'id']).groupby('application_type').count().orderBy('count', ascending=False).show(30)

+----------------+------+
|application_type| count|
+----------------+------+
|      INDIVIDUAL|886613|
|           JOINT|   511|
|             0.0|    72|
|            null|    61|
|             1.0|    58|
|        Jan-2016|     6|
|        May-2011|     3|
|        Dec-2011|     2|
|        Dec-2012|     2|
|        Feb-2012|     2|
|        Jul-2010|     2|
|        Jun-2011|     2|
|        Jun-2012|     2|
|               f|     1|
|           21.38|     1|
|         18131.0|     1|
|        Jan-2012|     1|
|        Aug-2012|     1|
|        Jan-2011|     1|
|        Mar-2011|     1|
|        Jun-2010|     1|
|        Oct-2015|     1|
|             6.0|     1|
|         1104.11|     1|
|          594.78|     1|
|          8000.0|     1|
|          1466.3|     1|
|            32.0|     1|
|           88.11|     1|
|           70.18|     1|
+----------------+------+
only showing top 30 rows



In [21]:
data.select(["pymnt_plan",'id']).groupby('pymnt_plan').count().orderBy('count', ascending=False).show(30)

+----------+------+
|pymnt_plan| count|
+----------+------+
|         n|887368|
|         y|    10|
|   Current|     1|
+----------+------+



In [22]:
0.1*887379

88737.90000000001

In [35]:
#there are 'joint' and 'individual'. for this analysis, we'll focus on individual application since they are the majority
df = data.filter(data.application_type == 'INDIVIDUAL')

In [36]:
df.count() 

886613

In [37]:
sample_df = df.sample(False, 0.1,seed)

In [29]:
annual_inc_sample_distribution = [go.Histogram(x=df.toPandas()['annual_inc'])]
iplot(annual_inc_sample_distribution, filename='annual_inc_sample_distribution')

In [38]:
sample_df.describe('annual_inc').show()

+-------+-----------------+
|summary|       annual_inc|
+-------+-----------------+
|  count|            88686|
|   mean|75014.98742721509|
| stddev|68789.70663682588|
|    min|          10000.0|
|    max|          99999.0|
+-------+-----------------+



In [39]:
df.describe('annual_inc').show()

+-------+-----------------+
|summary|       annual_inc|
+-------+-----------------+
|  count|           886609|
|   mean| 75036.9630256853|
| stddev|64710.72016786733|
|    min|          10000.0|
|    max|         999999.0|
+-------+-----------------+



In [56]:
75036.9630256853+64710.72016786733

139747.68319355263

In [46]:
df.filter(df['annual_inc'] ==999999.0).count()

1

In [47]:
df1 = df.filter(df.annual_inc <999999.0)
df1.count()

886426

In [49]:
sample_df1 = df1.sample(False, 0.1,seed)
df1.describe('annual_inc').show()

+-------+-----------------+
|summary|       annual_inc|
+-------+-----------------+
|  count|           886426|
|   mean|74583.24684546687|
| stddev|48069.70607926834|
|    min|          10000.0|
|    max|          99999.9|
+-------+-----------------+



In [53]:

sample_df1.select(["installment",'id']).groupby('installment').count().orderBy('count', ascending=False).show(30)

+-----------+-----+
|installment|count|
+-----------+-----+
|     327.34|  247|
|     318.79|  211|
|     392.81|  185|
|     491.01|  184|
|     312.86|  161|
|     322.63|  153|
|     654.68|  151|
|     478.19|  149|
|     382.55|  144|
|      314.2|  143|
|     196.41|  142|
|      332.1|  131|
|     261.88|  131|
|     163.67|  131|
|     375.43|  125|
|      336.9|  121|
|     637.58|  120|
|     335.45|  119|
|      159.4|  117|
|     329.91|  116|
|     387.15|  113|
|     333.53|  112|
|     469.29|  111|
|     625.72|  110|
|      471.3|  109|
|     255.04|  109|
|     482.23|  108|
|     191.28|  106|
|     483.94|  106|
|     498.15|  100|
+-----------+-----+
only showing top 30 rows



In [54]:
sample_df1.select(["mths_since_last_record",'id']).groupby('mths_since_last_record').count().orderBy('count', ascending=False).show(30)

+----------------------+-----+
|mths_since_last_record|count|
+----------------------+-----+
|                  null|74930|
|                  79.0|  213|
|                  64.0|  207|
|                  70.0|  201|
|                  69.0|  200|
|                  72.0|  199|
|                  71.0|  197|
|                  65.0|  194|
|                  68.0|  194|
|                  67.0|  192|
|                  55.0|  190|
|                  74.0|  188|
|                  60.0|  186|
|                  62.0|  183|
|                  61.0|  183|
|                  78.0|  183|
|                  53.0|  181|
|                  54.0|  180|
|                  66.0|  180|
|                  75.0|  180|
|                  58.0|  176|
|                  76.0|  172|
|                  56.0|  171|
|                  63.0|  170|
|                  52.0|  167|
|                  59.0|  166|
|                  81.0|  165|
|                  49.0|  160|
|                  77.0|  160|
|       

In [55]:
sample_df1.select(["revol_util",'id']).groupby('revol_util').count().orderBy('count', ascending=False).show(30)

+----------+-----+
|revol_util|count|
+----------+-----+
|       0.0|  390|
|      57.0|  196|
|      58.0|  194|
|      59.0|  186|
|      62.0|  185|
|      53.0|  184|
|      47.0|  180|
|      68.0|  177|
|      66.0|  172|
|      55.0|  172|
|      72.0|  170|
|      60.0|  170|
|      48.0|  169|
|      65.0|  169|
|      52.0|  169|
|      56.0|  169|
|      70.0|  167|
|      49.0|  162|
|      54.0|  162|
|      54.1|  161|
|      61.0|  159|
|      69.0|  158|
|      63.0|  158|
|      73.0|  158|
|      55.2|  158|
|      51.0|  154|
|      44.0|  152|
|      60.7|  152|
|      68.8|  151|
|      50.0|  151|
+----------+-----+
only showing top 30 rows



In [125]:
sample_df1.select(["next_pymnt_d",'id']).groupby('next_pymnt_d').count().orderBy('count', ascending=False).show(10)

+------------+-----+
|next_pymnt_d|count|
+------------+-----+
|    Feb-2016|55293|
|        null|25276|
|    Jan-2016| 7796|
|    Mar-2011|   16|
|    Jan-2011|   12|
|    Apr-2011|   12|
|    Feb-2011|   11|
|    May-2011|   10|
|    Mar-2016|    9|
|    Apr-2010|    8|
+------------+-----+
only showing top 10 rows



In [83]:
from pyspark.sql import functions as F
from pyspark.sql import types as T

df1 = df1.withColumn('annual_inc', F.round(F.col('annual_inc')).cast(T.IntegerType()))


In [84]:
def income_split(income):
    if income <= 75000:
        return 1
    elif 75000 < income <= 140000:
        return 2
    else:
        return 3

In [85]:
income_split_udf = udf(lambda x: income_split(x), StringType())
spark.udf.register("income_cat_split", income_split)
df1.select("annual_inc", income_split_udf('annual_inc').alias("income_category")).show(10)

<function __main__.income_split(income)>

+----------+---------------+
|annual_inc|income_category|
+----------+---------------+
|     24000|              1|
|     30000|              1|
|     12252|              1|
|     49200|              1|
|     80000|              2|
|     36000|              1|
|     47004|              1|
|     48000|              1|
|     40000|              1|
|     15000|              1|
+----------+---------------+
only showing top 10 rows



In [89]:
# Determining the loans that are bad from loan_status column

bad_loan = ["Charged Off", "Default", "Does not meet the credit policy. Status:Charged Off", "In Grace Period", 
            "Late (16-30 days)", "Late (31-120 days)"]

def loan_condition_int(status):
    if status in bad_loan:
        return 0
    else:
        return 1

In [91]:
loan_condition_int_udf = udf(lambda x: loan_condition_int(x), StringType())
spark.udf.register("loan_condition_binary_int", loan_condition_int)
df1.select("loan_status", loan_condition_int_udf('loan_status').alias("loan_condition_int")).show(10)


<function __main__.loan_condition_int(status)>

+-----------+------------------+
|loan_status|loan_condition_int|
+-----------+------------------+
| Fully Paid|                 1|
|Charged Off|                 0|
| Fully Paid|                 1|
| Fully Paid|                 1|
|    Current|                 1|
| Fully Paid|                 1|
|    Current|                 1|
| Fully Paid|                 1|
|Charged Off|                 0|
|Charged Off|                 0|
+-----------+------------------+
only showing top 10 rows



In [102]:
df1.describe('int_rate').show()

+-------+------------------+
|summary|          int_rate|
+-------+------------------+
|  count|            886426|
|   mean|13.246245631346063|
| stddev| 4.381966846349518|
|    min|              5.32|
|    max|             28.99|
+-------+------------------+



In [103]:
int_rate_sample_distribution = [go.Histogram(x=sample_df1.toPandas()['int_rate'])]
iplot(int_rate_sample_distribution, filename='int_rate_sample_distribution')

In [92]:
df2 = df1.withColumn("loan_condition", loan_condition_int_udf("loan_status"))
df3 = df2.withColumn("income_category", income_split_udf("annual_inc"))


In [126]:
raw_variables = ['id', 'loan_amnt', 'annual_inc', 'term', 'int_rate', 'installment', 'grade',
       'home_ownership', 'verification_status',
       'purpose', 'dti', 'delinq_2yrs', 'inq_last_6mths',
       'mths_since_last_delinq', 'mths_since_last_record', 'open_acc',
       'revol_bal', 'revol_util', 'total_acc', 'income_category',
       'loan_condition']

In [127]:
df4 = df3.select(raw_variables)
sample_df4 = df4.sample(False, 0.1,seed)

In [106]:
sample_df4_bad_loan = sample_df4.filter(sample_df4.loan_condition == 0)
sample_df4_good_loan = sample_df4.filter(sample_df4.loan_condition == 1)

In [108]:
int_rate_by_loan_cond_distribution = [
        go.Histogram(x=sample_df4_bad_loan.toPandas()['int_rate'], name="Bad Loan"),
        go.Histogram(x=sample_df4_good_loan.toPandas()['int_rate'], name="Good Loan")
    ]

iplot(int_rate_by_loan_cond_distribution, filename="spark/int_rate_by_loan_cond_distribution")

In [105]:
sample_df4.show(2)

+-------+---------+----------+--------+-----------+-----+--------------+----------+-------------------+-----------+-----+-----------+--------------+----------------------+----------------------+--------+---------+----------+---------+---------------+--------------+
|     id|loan_amnt|      term|int_rate|installment|grade|home_ownership|annual_inc|verification_status|    purpose|  dti|delinq_2yrs|inq_last_6mths|mths_since_last_delinq|mths_since_last_record|open_acc|revol_bal|revol_util|total_acc|income_category|loan_condition|
+-------+---------+----------+--------+-----------+-----+--------------+----------+-------------------+-----------+-----+-----------+--------------+----------------------+----------------------+--------+---------+----------+---------+---------------+--------------+
|1069866|   3000.0| 36 months|    9.91|      96.68|    B|          RENT|     15000|    Source Verified|credit_card|12.56|        0.0|           2.0|                  null|                  null|    11.0

In [111]:
#check which variables have null values
df4.select(*(sum(col(c).isNull().cast("int")).alias(c) for c in df4.columns)).show()

+---+---------+----+--------+-----------+-----+--------------+----------+-------------------+-------+---+-----------+--------------+----------------------+----------------------+--------+---------+----------+---------+---------------+--------------+
| id|loan_amnt|term|int_rate|installment|grade|home_ownership|annual_inc|verification_status|purpose|dti|delinq_2yrs|inq_last_6mths|mths_since_last_delinq|mths_since_last_record|open_acc|revol_bal|revol_util|total_acc|income_category|loan_condition|
+---+---------+----+--------+-----------+-----+--------------+----------+-------------------+-------+---+-----------+--------------+----------------------+----------------------+--------+---------+----------+---------+---------------+--------------+
|  0|        0|   0|       0|          0|    0|             0|         0|                  0|      0|  0|         25|            25|                453838|                749539|      25|        0|       497|       25|              0|             0|


In [117]:
sample_df4.describe('total_acc').show()

+-------+-----------------+
|summary|        total_acc|
+-------+-----------------+
|  count|            88664|
|   mean|25.23319498330777|
| stddev|11.86007434085358|
|    min|              1.0|
|    max|             98.0|
+-------+-----------------+



In [123]:
sample_df4.describe('revol_util').show()

+-------+------------------+
|summary|        revol_util|
+-------+------------------+
|  count|             88621|
|   mean| 55.10006352896033|
| stddev|23.876899648535847|
|    min|               0.0|
|    max|              99.9|
+-------+------------------+



In [129]:
df4.describe('delinq_2yrs').show()

+-------+------------------+
|summary|       delinq_2yrs|
+-------+------------------+
|  count|            886401|
|   mean|0.3144310532140645|
| stddev|0.8622683152282234|
|    min|               0.0|
|    max|               9.0|
+-------+------------------+



In [132]:
df4.describe('inq_last_6mths').show()

+-------+------------------+
|summary|    inq_last_6mths|
+-------+------------------+
|  count|            886401|
|   mean|0.6945073392290848|
| stddev|0.9981915890365933|
|    min|               0.0|
|    max|               9.0|
+-------+------------------+



In [133]:
df4.describe('mths_since_last_delinq').show()

+-------+----------------------+
|summary|mths_since_last_delinq|
+-------+----------------------+
|  count|                432588|
|   mean|    34.067401314876975|
| stddev|     21.88567141746072|
|    min|                   0.0|
|    max|                  99.0|
+-------+----------------------+



In [134]:
df4.describe('mths_since_last_record').show()

+-------+----------------------+
|summary|mths_since_last_record|
+-------+----------------------+
|  count|                136887|
|   mean|     70.12498630257073|
| stddev|     28.12330429823953|
|    min|                   0.0|
|    max|                  99.0|
+-------+----------------------+



In [135]:
df4.describe('open_acc').show()

+-------+------------------+
|summary|          open_acc|
+-------+------------------+
|  count|            886401|
|   mean|11.548986294013657|
| stddev|  5.31722105916296|
|    min|               0.0|
|    max|              90.0|
+-------+------------------+



In [137]:
df4.select('total_acc').show(5)

+---------+
|total_acc|
+---------+
|      9.0|
|      4.0|
|     10.0|
|     37.0|
|     38.0|
+---------+
only showing top 5 rows



In [ ]:
sample_df4.select(["revol_util",'loan_condition']).groupby("total_acc", "median")

In [138]:
sample_df4.printSchema()

root
 |-- id: integer (nullable = true)
 |-- loan_amnt: double (nullable = true)
 |-- annual_inc: integer (nullable = true)
 |-- term: string (nullable = true)
 |-- int_rate: double (nullable = true)
 |-- installment: double (nullable = true)
 |-- grade: string (nullable = true)
 |-- home_ownership: string (nullable = true)
 |-- verification_status: string (nullable = true)
 |-- purpose: string (nullable = true)
 |-- dti: string (nullable = true)
 |-- delinq_2yrs: string (nullable = true)
 |-- inq_last_6mths: string (nullable = true)
 |-- mths_since_last_delinq: string (nullable = true)
 |-- mths_since_last_record: string (nullable = true)
 |-- open_acc: string (nullable = true)
 |-- revol_bal: string (nullable = true)
 |-- revol_util: string (nullable = true)
 |-- total_acc: string (nullable = true)
 |-- income_category: string (nullable = true)
 |-- loan_condition: string (nullable = true)



In [141]:
impute_col= ['total_acc', 'inq_last_6mths', "revol_util", "delinq_2yrs", 'open_acc','mths_since_last_record', 'mths_since_last_delinq']
# change data type to float
for col in impute_col:
    df4 = df4.withColumn(col, df4[col].cast(FloatType()))


In [142]:
#impute missing values with the median (instead of mean), since these variables have rather extreme outliers
from pyspark.ml.feature import Imputer

median_imputer = Imputer(strategy='median', inputCols=['total_acc', 'inq_last_6mths', "revol_util", "delinq_2yrs", 'open_acc'], \
                  outputCols=['total_acc_imputed', 'inq_last_6mths_imputed',"revol_util_imputed", "delinq_2yrs_imputed", 'open_acc_imputed'])
median_model = median_imputer.fit(df4)

df5 = median_model.transform(df4)
df5.show(5)

+-------+---------+----------+----------+--------+-----------+-----+--------------+-------------------+--------------+-----+-----------+--------------+----------------------+----------------------+--------+---------+----------+---------+---------------+--------------+----------------------+-----------------+----------------+------------------+-------------------+
|     id|loan_amnt|annual_inc|      term|int_rate|installment|grade|home_ownership|verification_status|       purpose|  dti|delinq_2yrs|inq_last_6mths|mths_since_last_delinq|mths_since_last_record|open_acc|revol_bal|revol_util|total_acc|income_category|loan_condition|inq_last_6mths_imputed|total_acc_imputed|open_acc_imputed|revol_util_imputed|delinq_2yrs_imputed|
+-------+---------+----------+----------+--------+-----------+-----+--------------+-------------------+--------------+-----+-----------+--------------+----------------------+----------------------+--------+---------+----------+---------+---------------+--------------+

In [145]:
#replace missing values of each variable with their corresponding mean since ther
mean_imputer = Imputer(strategy='mean', inputCols=['mths_since_last_record', 'mths_since_last_delinq'],\
                  outputCols=['mths_since_last_record_imputed', 'mths_since_last_delinq_imputed'])
mean_model = mean_imputer.fit(df5)

df6 = mean_model.transform(df5)
df6.show(1)

+-------+---------+----------+----------+--------+-----------+-----+--------------+-------------------+-----------+-----+-----------+--------------+----------------------+----------------------+--------+---------+----------+---------+---------------+--------------+----------------------+-----------------+----------------+------------------+-------------------+------------------------------+------------------------------+
|     id|loan_amnt|annual_inc|      term|int_rate|installment|grade|home_ownership|verification_status|    purpose|  dti|delinq_2yrs|inq_last_6mths|mths_since_last_delinq|mths_since_last_record|open_acc|revol_bal|revol_util|total_acc|income_category|loan_condition|inq_last_6mths_imputed|total_acc_imputed|open_acc_imputed|revol_util_imputed|delinq_2yrs_imputed|mths_since_last_record_imputed|mths_since_last_delinq_imputed|
+-------+---------+----------+----------+--------+-----------+-----+--------------+-------------------+-----------+-----+-----------+--------------+--

In [148]:
pandas_df6 = df6.toPandas()

In [149]:
pandas_df6.head(1)

id  loan_amnt  annual_inc        term  int_rate  installment grade  \
0  1077501 5000.00     24000        36 months 10.65     162.87        B      

  home_ownership verification_status      purpose    dti  delinq_2yrs  \
0  RENT           Verified            credit_card  27.65 0.00           

   inq_last_6mths  mths_since_last_delinq  mths_since_last_record  open_acc  \
0 1.00            nan                     nan                     3.00        

  revol_bal  revol_util  total_acc income_category loan_condition  \
0  13648.0  83.70       9.00        1               1               

   inq_last_6mths_imputed  total_acc_imputed  open_acc_imputed  \
0 1.00                    9.00               3.00                

   revol_util_imputed  delinq_2yrs_imputed  mths_since_last_record_imputed  \
0 83.70               0.00                 70.12                             

   mths_since_last_delinq_imputed  
0 34.07

In [160]:
with open('../data/processed/pandas_df6.pkl', 'wb') as to_write:
    pickle.dump(pandas_df6, to_write)

In [5]:
sample_df6 = pandas_df6.sample(frac=0.1, replace=False, random_state=seed)


In [12]:
loan_amnt_sample_distribution = [go.Histogram(x=sample_df6['loan_amnt'])]
iplot(loan_amnt_sample_distribution, filename='loan_amnt_sample_distribution')


In [13]:
pandas_df6['loan_amnt'].describe()

count   886426.00
mean    14751.85 
std     8433.36  
min     500.00   
25%     8000.00  
50%     13000.00 
75%     20000.00 
max     35000.00 
Name: loan_amnt, dtype: float64

In [ ]:
data.agg(approx_count_distinct(data.emp_title).alias('distinct_emp_title')).collect()